In [445]:
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from pytorch_tabnet.tab_model import TabNetClassifier
#from pytorch_tabnet.tab_model import TabNetModel
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
import optuna
import torch
from sklearn import svm
import tensorflow as tf
from tensorflow import feature_column
from tensorflow.keras import layers
from tqdm.auto import tqdm
from pytorch_tabnet.tab_model import TabNetRegressor
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_validate
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer
from sklearn.decomposition import PCA

In [7]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

In [273]:
train_data = pd.read_csv("./train.csv")

In [274]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

In [275]:
train_data = train_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE'], axis = 1)

In [276]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

82


In [277]:
train_data.drop(colls, inplace = True, axis = 1)

In [278]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  \
0          1   0.533433  T050304            1   NaN   NaN  NaN   NaN   NaN   
1          2   0.541819  T050307            1   NaN   NaN  NaN   NaN   NaN   
2          1   0.531267  T050304            1   NaN   NaN  NaN   NaN   NaN   
3          2   0.537325  T050307            1   NaN   NaN  NaN   NaN   NaN   
4          1   0.531590  T050304            1   NaN   NaN  NaN   NaN   NaN   
..       ...        ...      ...          ...   ...   ...  ...   ...   ...   
593        1   0.526546  T100306            2   2.0  95.0  0.0  45.0  10.0   
594        0   0.524022  T050304            1   NaN   NaN  NaN   NaN   NaN   
595        0   0.521289  T050304            1   NaN   NaN  NaN   NaN   NaN   
596        1   0.531375  T100304            3  40.0  94.0  0.0  45.0  11.0   
597        1   0.533702  T100306            3  21.0  87.0  0.0  45.0  10.0   

     X_6   X_7   X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16  \
0    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
1    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
2    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
3    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
4    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
..   ...   ...   ...   ...   ...    ...    ...    ...   ...   ...    ...   
593  0.0  50.0  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5   
594  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
595  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
596  0.0  45.0  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5   
597  0.0  61.0  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5   

      X_17   X_18   X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27  \
0      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...   ...   ...   ...    ...    ...   
593  248.0  247.3  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
596  248.1  247.3  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0   
597  248.0  247.3  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0   

      X_28   X_29   X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
597  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   

      X_38  X_39  X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  \
0      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN   NaN 

In [279]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

In [280]:
T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [281]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == len(T050304) :
        T050304_col.append(col)
print(len(T050304_col))

T050304.drop(T050304_col, inplace = True, axis = 1)

825


In [282]:
T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == len(T050307) :
        T050307_col.append(col)
print(len(T050307_col))

T050307.drop(T050307_col, inplace = True, axis = 1)

818


In [283]:
T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == len(T010305) :
        T010305_col.append(col)
print(len(T010305_col))

T010305.drop(T010305_col, inplace = True, axis = 1)

1907


In [284]:
T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == len(T010306) :
        T010306_col.append(col)
print(len(T010306_col))

T010306.drop(T010306_col, inplace = True, axis = 1)

1907


In [285]:
T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == len(T100304) :
        T100304_col.append(col)
print(len(T100304_col))

T100304.drop(T100304_col, inplace = True, axis = 1)

2122


In [286]:
T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == len(T100306) :
        T100306_col.append(col)
print(len(T100306_col))

T100306.drop(T100306_col, inplace = True, axis = 1)

2122


In [287]:
T051 = list(set(T050307_col)-set(T050304_col))
T052 = list(set(T050304_col)-set(T050307_col))
T5drop = T051 + T052

T011 = list(set(T010305_col)-set(T010306_col))
T012 = list(set(T010306_col)-set(T010305_col))
T0drop = T011 + T012

T101 = list(set(T100304_col)-set(T100306_col))
T102 = list(set(T100306_col)-set(T100304_col))
T1drop = T101 + T102

In [288]:
T05 = pd.concat([T050304, T050307])
T01 = pd.concat([T010305, T010306])
T10 = pd.concat([T100304, T100306])

In [289]:
T05.drop(T5drop, inplace = True, axis = 1)
T01.drop(T0drop, inplace = True, axis = 1)
T10.drop(T1drop, inplace = True, axis = 1)

In [290]:
T05 = T05.fillna(0)
T01 = T01.fillna(0)
T10 = T10.fillna(0)

In [291]:
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)#.to_numpy()
T05_target = T05['Y_Class']#.to_numpy()

In [292]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
0             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
1             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
2             0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
3             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
4             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
..            ...    ...    ...    ...    ...       ...       ...       ...   
115           0.0   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
118           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
119           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   

        X_139     X_140     X_141  X_142  X_143  X_144  X_145     X_146  \
0   -0.024793 -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454   
1    0.024793 -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040   
2   -0.008264 -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877   
3    0.002755 -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990   
4   -0.002755 -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680   
..        ...       ...       ...    ...    ...    ...    ...       ...   
115 -1.049587 -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057   
116 -1.049587 -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895   
117 -1.044077 -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307   
118 -1.033058 -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895   
119 -1.082645 -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921   

     X_147     X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  \
0      0.0  0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0   
1      0.0 -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0   
2      0.0  0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0   
3      0.0  0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0   
4      0.0  0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0   
..     ...       ...       ...     ...    ...    ...    ...    ...    ...   
115    0.0  1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0   
116    0.0  1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0   
117    0.0  1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0   
118    0.0  1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0   
119    0.0  1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0   

     X_156  X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  \
0      0.0    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
1      0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
2      0.1    0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5   
3      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5   
4      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
115    0.0    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
116    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5   
117    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5   
118    0.0   -0.1    0.0   -1.0    0.1    0.0    0.0   -0.1    0.0   -0.5   
119    0.0    0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0.5   

     X_166  X_167  X_168  X_169  X_170  X_171  X_172  X_173  X_174  X_175  \
0      0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1      0.0   -1.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0   
2      0.0   -1.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0 

In [293]:
T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Class'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Class'], axis = 1, inplace = True)
T05_data

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
index                                                                           
0               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
2               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
4               0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
6               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
8               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
...             ...    ...    ...    ...    ...       ...       ...       ...   
549             0.0   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292   
550             0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
551             0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
552             0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
555             0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   

          X_139     X_140     X_141  X_142  X_143  X_144  X_145     X_146  \
index                                                                       
0     -0.024793 -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454   
2      0.024793 -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040   
4     -0.008264 -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877   
6      0.002755 -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990   
8     -0.002755 -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680   
...         ...       ...       ...    ...    ...    ...    ...       ...   
549   -1.049587 -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057   
550   -1.049587 -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895   
551   -1.044077 -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307   
552   -1.033058 -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895   
555   -1.082645 -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921   

       X_147     X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  \
index                                                                         
0        0.0  0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0   
2        0.0 -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0   
4        0.0  0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0   
6        0.0  0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0   
8        0.0  0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0   
...      ...       ...       ...     ...    ...    ...    ...    ...    ...   
549      0.0  1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0   
550      0.0  1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0   
551      0.0  1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0   
552      0.0  1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0   
555      0.0  1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0   

       X_156  X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  \
index                                                                         
0        0.0    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
2        0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
4        0.1    0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5   
6        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5   
8        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549      0.0    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
550      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5   
551      0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5   
552      0.0   -0.1    0.0   -1.0    0.1    0.0    0.0

In [294]:
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)#.to_numpy()
T01_target = T01['Y_Class']#.to_numpy()

In [295]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

PRODUCT_CODE  X_246  X_247     X_248  X_249  X_250     X_251  X_252  \
0             0.0    0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   
1             0.0    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   
2             0.0    0.0   1.25 -0.054348    0.0    0.0  1.146067    0.0   
3             0.0    0.0   1.25 -0.054348    0.0    0.0  1.179775    0.0   
4             0.0    0.0  -0.75 -0.054348    0.0    0.0  1.179775    0.0   
..            ...    ...    ...       ...    ...    ...       ...    ...   
124           0.0    0.0   0.75  1.108696    0.0    0.0  0.000000    0.0   
125           0.0    1.0   1.25  1.293478    0.0    0.0  0.000000    0.0   
126           0.0    0.0  -0.25  1.423913    0.0    1.0  0.000000    0.0   
127           0.0    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0   
128           0.0    0.0   0.75  0.630435    0.0    1.0  0.000000    0.0   

     X_253  X_254  X_255     X_256     X_257     X_258  X_259  X_260  \
0     -1.0   -1.0    0.0 -0.145455 -0.198381 -0.068571    0.0    0.0   
1     -1.0   -1.0    0.0 -0.131818 -0.137652 -0.125714    0.0    0.0   
2      0.0   -1.0    0.0 -0.072727 -0.097166 -0.085714    0.0    0.0   
3     -1.0   -1.0    0.0  0.031818  0.000000  0.000000    0.0    0.0   
4     -1.0   -1.0    0.0  0.027273  0.000000  0.057143    0.0    0.0   
..     ...    ...    ...       ...       ...       ...    ...    ...   
124    0.0    0.0    0.0  0.068182  0.048583  0.154286    0.0    0.0   
125    0.0    0.0    0.0  0.295455  0.246964  0.462857    0.0    0.0   
126    0.0    0.0    0.0  0.459091  0.421053  0.657143    0.0    0.0   
127    0.0    0.0    0.0  0.568182  0.481781  0.697143    0.0    0.0   
128    0.0    0.0    0.0 -0.172727 -0.234818  0.000000    0.0    0.0   

        X_261  X_262  X_263  X_264     X_265     X_266     X_267  X_268  \
0   -0.333333  -0.75 -0.250    0.0  0.095238  0.105263  0.125000    0.0   
1   -0.666667  -1.00  0.000    0.0  0.047619  0.105263  0.083333    0.0   
2   -0.666667  -1.50 -0.250    0.0  0.000000  0.105263 -0.041667    0.0   
3    0.666667   0.25  0.250    0.0 -0.095238 -0.052632 -0.083333    0.0   
4    0.666667   0.00  0.625    0.0 -0.095238  0.000000 -0.083333    0.0   
..        ...    ...    ...    ...       ...       ...       ...    ...   
124 -1.000000   0.25 -1.000    0.0 -0.047619  0.000000 -0.041667   -1.0   
125 -1.000000  -0.25 -0.500    0.0 -0.285714 -0.210526 -0.291667   -1.0   
126 -1.000000   0.25 -0.875    0.0 -0.476190 -0.368421 -0.458333    0.0   
127  0.000000   0.75 -0.625    0.0 -0.523810 -0.526316 -0.541667   -1.0   
128 -2.000000  -0.50 -1.000    0.0  0.190476  0.210526  0.208333   -1.0   

     X_269  X_270  X_271  X_272  X_273  X_274  X_275  X_276  X_277  X_278  \
0      0.0    0.0    1.0    0.0    1.0    0.0    0.0    0.0    0.0    0.0   
1      0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
2      0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
3      0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
4      0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
124    0.0   -1.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.0   
125    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
126    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
127    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
128    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

     X_279  X_280  X_281  X_282  X_283  X_284  X_285  X_286     X_287  \
0      0.0    0.0    0.0    0.0    0.0    0.0    0.6    0.4  0.600000   
1      0.0    0.0    0.0    0.0    0.0    0.0    0.6    0.4  0.600000   
2      0.0    0.0    0.0    0.0   -0.5    0.0    0.6    0.4  0.600000   
3      0.0    0.0    0.0    0.0    0.0    0.0    0.6    0.4  0.600000   
4      1.0    0.0    1.0    0.0    0

In [296]:
T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Class'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Class'], axis = 1, inplace = True)
T01_data

PRODUCT_CODE  X_246  X_247     X_248  X_249  X_250     X_251  X_252  \
index                                                                        
28              0.0    0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   
33              0.0    0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   
39              0.0    0.0   1.25 -0.054348    0.0    0.0  1.146067    0.0   
40              0.0    0.0   1.25 -0.054348    0.0    0.0  1.179775    0.0   
41              0.0    0.0  -0.75 -0.054348    0.0    0.0  1.179775    0.0   
...             ...    ...    ...       ...    ...    ...       ...    ...   
479             0.0    0.0   0.75  1.108696    0.0    0.0  0.000000    0.0   
501             0.0    1.0   1.25  1.293478    0.0    0.0  0.000000    0.0   
523             0.0    0.0  -0.25  1.423913    0.0    1.0  0.000000    0.0   
531             0.0    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0   
585             0.0    0.0   0.75  0.630435    0.0    1.0  0.000000    0.0   

       X_253  X_254  X_255     X_256     X_257     X_258  X_259  X_260  \
index                                                                    
28      -1.0   -1.0    0.0 -0.145455 -0.198381 -0.068571    0.0    0.0   
33      -1.0   -1.0    0.0 -0.131818 -0.137652 -0.125714    0.0    0.0   
39       0.0   -1.0    0.0 -0.072727 -0.097166 -0.085714    0.0    0.0   
40      -1.0   -1.0    0.0  0.031818  0.000000  0.000000    0.0    0.0   
41      -1.0   -1.0    0.0  0.027273  0.000000  0.057143    0.0    0.0   
...      ...    ...    ...       ...       ...       ...    ...    ...   
479      0.0    0.0    0.0  0.068182  0.048583  0.154286    0.0    0.0   
501      0.0    0.0    0.0  0.295455  0.246964  0.462857    0.0    0.0   
523      0.0    0.0    0.0  0.459091  0.421053  0.657143    0.0    0.0   
531      0.0    0.0    0.0  0.568182  0.481781  0.697143    0.0    0.0   
585      0.0    0.0    0.0 -0.172727 -0.234818  0.000000    0.0    0.0   

          X_261  X_262  X_263  X_264     X_265     X_266     X_267  X_268  \
index                                                                       
28    -0.333333  -0.75 -0.250    0.0  0.095238  0.105263  0.125000    0.0   
33    -0.666667  -1.00  0.000    0.0  0.047619  0.105263  0.083333    0.0   
39    -0.666667  -1.50 -0.250    0.0  0.000000  0.105263 -0.041667    0.0   
40     0.666667   0.25  0.250    0.0 -0.095238 -0.052632 -0.083333    0.0   
41     0.666667   0.00  0.625    0.0 -0.095238  0.000000 -0.083333    0.0   
...         ...    ...    ...    ...       ...       ...       ...    ...   
479   -1.000000   0.25 -1.000    0.0 -0.047619  0.000000 -0.041667   -1.0   
501   -1.000000  -0.25 -0.500    0.0 -0.285714 -0.210526 -0.291667   -1.0   
523   -1.000000   0.25 -0.875    0.0 -0.476190 -0.368421 -0.458333    0.0   
531    0.000000   0.75 -0.625    0.0 -0.523810 -0.526316 -0.541667   -1.0   
585   -2.000000  -0.50 -1.000    0.0  0.190476  0.210526  0.208333   -1.0   

       X_269  X_270  X_271  X_272  X_273  X_274  X_275  X_276  X_277  X_278  \
index                                                                         
28       0.0    0.0    1.0    0.0    1.0    0.0    0.0    0.0    0.0    0.0   
33       0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
39       0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
40       0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
41       0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
479      0.0   -1.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.0   
501      0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
523      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
531      0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.0    1.0    0.0   
585      0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   


In [297]:
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)#.to_numpy()
T10_target = T10['Y_Class']#.to_numpy()

In [298]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

PRODUCT_CODE   X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  \
0             0.0   0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
1             0.0   0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
2             0.0   0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
3             0.0   0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
4             0.0   0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
..            ...   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...   
344           0.0  -1.0 -0.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0   
345           0.0  -1.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0   
346           0.0  -1.0 -1.6  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0   
347           0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0   
348           1.0  19.0 -1.6  0.0  0.0  0.0  0.0  2.666667  0.0  1.0   0.0   

         X_11      X_12      X_13  X_14  X_15  X_16  X_17  X_18  X_19  \
0    0.653153  0.746725  0.714286   0.0   0.0   0.0  -1.0  -1.0   0.0   
1    0.662162  0.768559  0.723214   0.0   0.0   1.0   0.0   1.0   0.0   
2    0.788288  0.917031  0.852679   0.0   0.0   0.0  -3.0   0.0   0.0   
3    0.747748  0.917031  0.790179   0.0   0.0   1.0   0.0   1.0   0.0   
4    0.792793  0.947598  0.830357   0.0   0.0   0.0   0.0  -1.0   0.0   
..        ...       ...       ...   ...   ...   ...   ...   ...   ...   
344 -1.549550 -1.519651 -1.504464   0.0   0.0   0.0  -1.0   0.0   0.0   
345 -1.527027 -1.506550 -1.419643   0.0   0.0   0.0  -1.0   0.0   0.0   
346 -1.531532 -1.506550 -1.473214   0.0   0.0   1.0  -1.0  -1.0   0.0   
347 -1.396396 -1.358079 -1.366071   0.0   0.0   0.0  -1.0   0.0   0.0   
348 -1.319820 -1.314410 -1.200893   0.0   0.0   0.0  -1.0   0.0   0.0   

         X_20      X_21      X_22  X_23  X_24  X_25  X_26  X_27  X_28  X_29  \
0   -0.636364 -0.652174 -0.727273   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
1   -0.636364 -0.695652 -0.727273   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
2   -0.772727 -0.826087 -0.909091   0.0  0.01   0.0   0.0   0.0   0.0   0.0   
3   -0.727273 -0.739130 -0.863636   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
4   -0.772727 -0.826087 -0.909091   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
..        ...       ...       ...   ...   ...   ...   ...   ...   ...   ...   
344  1.636364  1.565217  1.636364   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
345  1.590909  1.521739  1.636364   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
346  1.590909  1.608696  1.636364   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
347  1.454545  1.434783  1.454545   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
348  1.363636  1.260870  1.363636   0.0  0.01   0.0   0.0   0.0   0.0   0.0   

     X_30  X_31  X_32  X_33  X_34  X_35  X_36  X_37      X_38  X_39      X_40  \
0     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0  0.000000   
1     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0  0.000000   
2     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0 -0.230769   
3     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0 -0.230769   
4     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0 -0.230769   
..    ...   ...   ...   ...   ...   ...   ...   ...       ...   ...       ...   
344   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -1.000000   0.0  1.346154   
345   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -0.666667   0.0  1.346154   
346   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -1.000000   0.0  1.346154   
347   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -1.000000   0.0  1.346154   
348   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -0.333333  -1.0  1.346154   

         X_41      X_42      X_43      X_44  X_45      X_46      X_47  \
0   -0.185185 -0.473684  0.722222  0.000000   0.6 -0.125000  0.000000   
1   -0.185185 -0.473684  0.722222  0.000000   0.6 -0.125000  0.000000   
2   -0.370370 -0.210526  0.444444 -0.205882  -0.4 

In [299]:
T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Class'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Class'], axis = 1, inplace = True)
T10_data

PRODUCT_CODE   X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  \
index                                                                          
22              0.0   0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
23              0.0   0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
25              0.0   0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
29              0.0   0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
37              0.0   0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0   
...             ...   ...  ...  ...  ...  ...  ...       ...  ...  ...   ...   
589             0.0  -1.0 -0.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0   
590             0.0  -1.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0   
591             0.0  -1.0 -1.6  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0   
593             0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0   
597             1.0  19.0 -1.6  0.0  0.0  0.0  0.0  2.666667  0.0  1.0   0.0   

           X_11      X_12      X_13  X_14  X_15  X_16  X_17  X_18  X_19  \
index                                                                     
22     0.653153  0.746725  0.714286   0.0   0.0   0.0  -1.0  -1.0   0.0   
23     0.662162  0.768559  0.723214   0.0   0.0   1.0   0.0   1.0   0.0   
25     0.788288  0.917031  0.852679   0.0   0.0   0.0  -3.0   0.0   0.0   
29     0.747748  0.917031  0.790179   0.0   0.0   1.0   0.0   1.0   0.0   
37     0.792793  0.947598  0.830357   0.0   0.0   0.0   0.0  -1.0   0.0   
...         ...       ...       ...   ...   ...   ...   ...   ...   ...   
589   -1.549550 -1.519651 -1.504464   0.0   0.0   0.0  -1.0   0.0   0.0   
590   -1.527027 -1.506550 -1.419643   0.0   0.0   0.0  -1.0   0.0   0.0   
591   -1.531532 -1.506550 -1.473214   0.0   0.0   1.0  -1.0  -1.0   0.0   
593   -1.396396 -1.358079 -1.366071   0.0   0.0   0.0  -1.0   0.0   0.0   
597   -1.319820 -1.314410 -1.200893   0.0   0.0   0.0  -1.0   0.0   0.0   

           X_20      X_21      X_22  X_23  X_24  X_25  X_26  X_27  X_28  X_29  \
index                                                                           
22    -0.636364 -0.652174 -0.727273   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
23    -0.636364 -0.695652 -0.727273   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
25    -0.772727 -0.826087 -0.909091   0.0  0.01   0.0   0.0   0.0   0.0   0.0   
29    -0.727273 -0.739130 -0.863636   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
37    -0.772727 -0.826087 -0.909091   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
...         ...       ...       ...   ...   ...   ...   ...   ...   ...   ...   
589    1.636364  1.565217  1.636364   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
590    1.590909  1.521739  1.636364   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
591    1.590909  1.608696  1.636364   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
593    1.454545  1.434783  1.454545   0.0  0.00   0.0   0.0   0.0   0.0   0.0   
597    1.363636  1.260870  1.363636   0.0  0.01   0.0   0.0   0.0   0.0   0.0   

       X_30  X_31  X_32  X_33  X_34  X_35  X_36  X_37      X_38  X_39  \
index                                                                   
22      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0   
23      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0   
25      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0   
29      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0   
37      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.333333   0.0   
...     ...   ...   ...   ...   ...   ...   ...   ...       ...   ...   
589     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -1.000000   0.0   
590     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -0.666667   0.0   
591     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -1.000000   0.0   
593     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -1.000000   0.0   
597     0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0 -0.333

In [327]:
T05_data = T05_data.to_numpy()
T01_data = T01_data.to_numpy()
T10_data = T10_data.to_numpy()

# Test data

In [388]:
test_data = pd.read_csv("./test.csv")

In [389]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

In [390]:
test_data = test_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE'], axis = 1)

In [391]:
test_data.drop(colls, inplace = True, axis = 1)

In [392]:
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

         X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
0           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     2   
1           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     2   
2           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     8   
3    444.192308   423.0     NaN     NaN     NaN     NaN     NaN     NaN    10   
4    443.211539   423.0     NaN     NaN     NaN     NaN     NaN     NaN    11   
..          ...     ...     ...     ...     ...     ...     ...     ...   ...   
305         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    11   
306         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    16   
307         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    16   
308         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    20   
309         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    21   

     DAY_OF_WEEK  
0              5  
1              5  
2              5  
3              5  
4              5  
..           ...  
305            6  
306            6  
307            6  
308            6  
309            6  

[310 rows x 2797 columns]

In [393]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']
TT050304

LINE PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6  X_7  X_8  ...  \
7   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
8   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
14  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
35  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
41  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
42  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
52  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
53  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
54  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
61  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
64  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
65  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
66  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   

        X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
7   369.462963   354.0   57.74   52.51   54.45   57.99   63.16     1.0    12   
8   370.259259   353.0   53.18   56.02   41.79   47.94   60.72     1.0    12   
14  369.377359   353.0   49.77   54.93   49.85   48.62   63.18     1.0     6   
35  369.660377   352.0   55.22   58.14   48.93   56.16   64.25     1.0     3   
41  368.018519   352.0   49.67   45.00   49.81   55.19   67.17     1.0    23   
42  368.452830   353.0   51.30   47.66   60.00   53.75   62.58     1.0    23   
52  368.320755   353.0   54.06   51.18   52.17   57.75   63.94     1.0    17   
53  361.226415   342.0   54.04   51.25   54.98   57.22   63.33     1.0    17   
54  367.849057   352.0   55.72   57.57   42.08   55.19   66.06     1.0    18   
61  370.000000   354.0     NaN     NaN     NaN     NaN     NaN     1.0    21   
64  367.943396   352.0     NaN     NaN     NaN     NaN     NaN     1.0     0   
65  368.056604   352.0   51.55   55.55   39.85   47.82   61.59     1.0     3   
66  369.111111   353.0   51.37   55.70   52.49   48.34   62.12     1.0     8   

    DAY_OF_WEEK  
7             6  
8             6  
14            6  
35            7  
41            1  
42            1  
52            3  
53            3  
54            3  
61            7  
64            1  
65            1  
66            1  

[13 rows x 2797 columns]

In [394]:
TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [395]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7             1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8             1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14            1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35            1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41            1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42            1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52            1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53            1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54            1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61            1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64            1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65            1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66            1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  \
7   354.0  ...  369.462963   354.0   57.74   52.51   54.45   57.99   63.16   
8   355.0  ...  370.259259   353.0   53.18   56.02   41.79   47.94   60.72   
14   60.0  ...  369.377359   353.0   49.77   54.93   49.85   48.62   63.18   
35  249.0  ...  369.660377   352.0   55.22   58.14   48.93   56.16   64.25   
41  293.0  ...  368.018519   352.0   49.67   45.00   49.81   55.19   67.17   
42  293.0  ...  368.452830   353.0   51.30   47.66   60.00   53.75   62.58   
52  330.0  ...  368.320755   353.0   54.06   51.18   52.17   57.75   63.94   
53  330.0  ...  361.226415   342.0   54.04   51.25   54.98   57.22   63.33   
54  330.0  ...  367.849057   352.0   55.72   57.57   42.08   55.19   66.06   
61  436.0  ...  370.000000   354.0     NaN     NaN     NaN     NaN     NaN   
64  437.0  ...  367.943396   352.0     NaN     NaN     NaN     NaN     NaN   
65  441.0  ...  368.056604   352.0   51.55   55.55   39.85   47.82   61.59   
66  446.0  ...  369.111111   353.0   51.37   55.70   52.49   48.34   62.12   

    X_2871  HOUR  DAY_OF_WEEK  
7      1.0    12            6  
8      1.0    12            6  
14     1.0     6            6  
35     1.0     3            7  
41     1.0    23            1  
42     1.0    23            1  
52     1.0    17            3  
53     1.0    17            3  
54     1.0    18            3  
61     1.0    21            7  
64     1.0     0            1  
65     1.0     3            1  
66     1.0     8            1  

[13 rows x 1971 columns]

In [396]:
TT05 = pd.concat([TT050304, TT050307])
TT01 = pd.concat([TT010305, TT010306])
TT10 = pd.concat([TT100304, TT100306])

In [397]:
TT05.drop(T5drop, inplace = True, axis = 1)
TT01.drop(T0drop, inplace = True, axis = 1)
TT10.drop(T1drop, inplace = True, axis = 1)

In [398]:
TT05 = TT05.fillna(0)
TT01 = TT01.fillna(0)
TT10 = TT10.fillna(0)

In [399]:
TT05_idx = TT05['PRODUCT_CODE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])
TT05_idx

index
0       7
1       8
2      14
3      35
4      41
5      42
6      52
7      53
8      54
9      61
10     64
11     65
12     66
13     13
14     36
15     62
16     63
17    130
18    131
19    132
20    248
21    249
22    250
23    251
24    252
25    253
26    254
27    255
28    260
29    263
30    280
31    281
32    282
33    283
34    284
35    285
36    286
37    292
38    293

In [400]:
TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)
TT05

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
0            0.0   -1.0   -1.0   -1.0    0.0  0.055781  0.053753  0.053999   
1            0.0   -1.0   -1.0   -1.0    0.0  0.057809  0.053753  0.056037   
2            0.0   -1.0    0.0   -1.0    0.0 -0.540568 -0.542596 -0.545084   
3            0.0    0.0    0.0    0.0    0.0 -0.157201 -0.159229 -0.159959   
4            0.0    0.0    0.0    0.0    0.0 -0.067951 -0.069980 -0.070301   
5            0.0    0.0    0.0   -1.0    0.0 -0.067951 -0.069980 -0.070301   
6            0.0   -1.0    0.0   -1.0    0.0  0.007099  0.005071  0.005094   
7            0.0    0.0    0.0    0.0    0.0  0.007099  0.005071  0.005094   
8            0.0   -1.0    0.0   -1.0    0.0  0.007099  0.005071  0.005094   
9            0.0    0.0    0.0    0.0    0.0  0.222110  0.220081  0.221090   
10           0.0    0.0    0.0    0.0    0.0  0.224138  0.222110  0.223128   
11           0.0    0.0    0.0    0.0    0.0  0.232252  0.230223  0.231279   
12           0.0    0.0    0.0    0.0    0.0  0.242394  0.240365  0.241467   
13           0.0    1.0    1.0    1.0    0.0 -0.195740 -0.197769 -0.196638   
14           0.0    1.0    1.0    1.0    0.0 -0.461460 -0.463489 -0.465614   
15           0.0    1.0    1.0    1.0    0.0 -0.560852 -0.564909 -0.585838   
16           0.0    1.0    1.0    1.0    0.0 -0.556795 -0.560852 -0.583800   
17           0.0    1.0    1.0    0.0    0.0  0.197769  0.193712  0.174223   
18           0.0    1.0    0.0    1.0    0.0  0.197769  0.193712  0.176261   
19           0.0    1.0    1.0    1.0    0.0  0.201826  0.197769  0.180336   
20           0.0    1.0    1.0    1.0    0.0  0.822515  0.818458  0.803872   
21           0.0    1.0    1.0    1.0    0.0  0.822515  0.818458  0.803872   
22           0.0    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872   
23           0.0    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872   
24           0.0    1.0    1.0    1.0    0.0  0.824544  0.820487  0.803872   
25           0.0    1.0    1.0    1.0    0.0  0.824544  0.820487  0.805909   
26           0.0    1.0    1.0    1.0    0.0  0.832657  0.828600  0.814060   
27           0.0    1.0    1.0    1.0    0.0  0.834686  0.830629  0.814060   
28           0.0    1.0    1.0    0.0    0.0  0.834686  0.830629  0.816098   
29           0.0    0.0    1.0    0.0    0.0  0.840771  0.836714  0.820173   
30           0.0    1.0    1.0    1.0    0.0  0.938134  0.934077  0.920020   
31           0.0    1.0    1.0    1.0    0.0  0.940162  0.936105  0.920020   
32           0.0    1.0    1.0    1.0    0.0  0.960446  0.956389  0.940397   
33           0.0    1.0    1.0    1.0    0.0  0.960446  0.956389  0.942435   
34           0.0    1.0    1.0    1.0    0.0  0.972617  0.968560  0.954661   
35           0.0    1.0    1.0    1.0    0.0  0.972617  0.968560  0.954661   
36           0.0    1.0    1.0    1.0    0.0  0.974645  0.970588  0.954661   
37           0.0    1.0    1.0    1.0    0.0  1.003043  0.998986  0.983189   
38           0.0    1.0    1.0    1.0    0.0  1.003043  0.998986  0.985227   

       X_139     X_140  ...    X_2864  X_2865    X_2866    X_2867    X_2868  \
0   0.449036  0.428571  ...  0.739720     2.0  0.318280 -0.115314  0.320714   
1   0.449036  0.428571  ...  1.204775     1.0  0.036189  0.067832 -0.583571   
2  -1.374656 -1.195011  ...  0.689726     1.0 -0.174760  0.010957 -0.007857   
3  -0.013774 -0.052154  ...  0.855015     0.0  0.162388  0.178450 -0.073571   
4  -0.134986 -0.142857  ... -0.103867     0.0 -0.180946 -0.507175 -0.010714   
5  -0.129477 -0.138322  ...  0.149781     1.0 -0.080111 -0.368380  0.717143   
6  -0.024793 -0.015873  ...  0.072646     1.0  0.090628 -0.184712  0.157857   
7   0.002755 -0.011338  ... -4.070605   -10.0  0.089391 -0.181059  0.358571   
8  -0.019284 -0.020408  ... -0.202836     0.0  0.193319  0.148709 -0.562857   
9   0.482094  0.437642  ...  1.053362     2.0 -3.253634 -2.855205 -3.568571   
10  0.570248  

In [401]:
TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

In [402]:
TT01_idx = TT01['PRODUCT_CODE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])
TT01_idx

index
0       3
1       6
2      10
3      11
4      38
5      40
6      71
7      86
8      88
9      89
10    116
11    117
12    141
13    142
14      4
15      5
16      9
17     12
18     37
19     39
20     72
21     79
22     87
23    109
24    114
25    115
26    128
27    129

In [403]:
TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)
TT01

PRODUCT_CODE  X_246  X_247     X_248  X_249  X_250     X_251  X_252  \
0            0.0    0.0   0.75 -0.054348    0.0    0.0  0.415730    0.0   
1            0.0    0.0   0.75 -0.054348    0.0    0.0  0.449438    0.0   
2            0.0    0.0   0.00 -0.054348    0.0    0.0  0.516854    0.0   
3            0.0    0.0   1.25 -0.054348    0.0    0.0  0.595506    0.0   
4            0.0    1.0  -0.50 -0.054348    0.0    0.0  1.505618    0.0   
5            0.0    1.0   0.75 -0.054348    0.0    0.0  1.584270    0.0   
6            0.0    1.0  -0.25 -0.054348    0.0    0.0  0.067416    0.0   
7            0.0    0.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   
8            0.0   16.0   0.00 -0.054348    0.0    0.0  0.258427    0.0   
9            0.0    1.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   
10           0.0    1.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   
11           0.0    0.0  -0.50 -0.054348    0.0    0.0  0.483146    0.0   
12           0.0    0.0  -0.50 -0.054348    0.0    0.0  0.775281    0.0   
13           0.0    1.0  -0.75 -0.054348    0.0    0.0  0.775281    0.0   
14           0.0    1.0   1.25  0.913043    0.0    1.0  0.000000    0.0   
15           0.0    1.0   0.00  0.945652    0.0    1.0  0.000000    0.0   
16           0.0    0.0  -0.25  1.010870    0.0    0.0  0.000000    0.0   
17           0.0    1.0  -0.25  1.086957    0.0    0.0  0.000000    0.0   
18           0.0    0.0   1.00  0.097826    0.0    1.0  0.000000    0.0   
19           0.0    1.0   0.25  0.173913    0.0    1.0  0.000000    0.0   
20           0.0    1.0   1.75  0.902174    0.0    1.0  0.000000    0.0   
21           0.0    0.0   0.00  0.956522    0.0    1.0  0.000000    0.0   
22           0.0    0.0   0.50  1.152174    0.0    1.0  0.000000    0.0   
23           0.0    3.0   1.75  1.326087    0.0    1.0  0.000000    0.0   
24           0.0    0.0   1.25  1.358696    0.0    1.0  0.000000    0.0   
25           0.0    1.0   0.75  1.358696    0.0    1.0  0.000000    0.0   
26           0.0    0.0   1.25  1.500000    0.0    1.0  0.000000    0.0   
27           0.0    1.0   0.75  1.500000    0.0    1.0  0.000000    0.0   

    X_253  X_254  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
0    -1.0   -1.0  ... -0.585118 -1.336788  1.159091  1.715374  1.636986   
1    -1.0   -1.0  ... -1.705924 -2.854922  1.424242  1.957184  1.041096   
2    -1.0   -1.0  ... -0.951125 -0.829016  1.204545  1.582338  0.993151   
3    -1.0   -1.0  ... -1.343554 -1.497409  1.090909  1.374600  1.109589   
4    -1.0   -1.0  ... -1.920884 -2.207254  0.954545  1.398276  1.383562   
5    -1.0   -1.0  ... -1.380046 -1.658031  1.628788  2.220402  1.767123   
6    -1.0   -1.0  ... -0.420824 -0.549223  1.492424  2.167816  1.863014   
7    -1.0   -1.0  ...  0.051022 -0.720207  1.492424  2.143966  1.369863   
8    -1.0   -1.0  ...  5.506263  3.642487  3.325758  3.852278  3.178082   
9    -1.0   -1.0  ...  0.291414  0.010363  1.446970  2.243647  1.671233   
10   -1.0   -1.0  ... -1.391573 -2.569948  1.416667  1.918647  1.561644   
11   -1.0   -1.0  ... -1.849230 -1.870466  1.750000  2.069828  1.993151   
12   -1.0   -1.0  ...  2.704854  1.316062  1.727273  2.173563  2.089041   
13    0.0   -1.0  ...  3.291153  2.523316  2.484848  2.879659  2.452055   
14    0.0    0.0  ...  0.117716 -0.689119  2.083333  1.851385  1.356164   
15    0.0    0.0  ... -1.153107 -1.388601  1.560606  1.792529  1.493151   
16    0.0    0.0  ... -0.074593  0.113990  1.083333  1.794540  1.684932   
17    0.0    0.0  ... -1.159318 -1.233161  1.090909  1.678161  1.801370   
18    0.0    0.0  ... -0.302514 -0.854922  1.106061  1.346921  0.883562   
19    0.0    0.0  ... -1.664884 -2.062176  1.825758  2.331897  1.856164   
20    0.0    0.0  ... -0.311680 -1.683938  1.772727  2.225575  1.315068   
21    0.0    0.0  ... -1.083228 -1.735751  1.568182  2.054598  2.157534   
22    0.0    0.0  ...  1.266465 -0.082902  1.833333  2.227299  1.904110   
23    0.0    0.0  ...  3.018

In [404]:
TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')
TT01

PRODUCT_CODE  X_246  X_247     X_248  X_249  X_250     X_251  X_252  \
index                                                                        
3               0.0    0.0   0.75 -0.054348    0.0    0.0  0.415730    0.0   
6               0.0    0.0   0.75 -0.054348    0.0    0.0  0.449438    0.0   
10              0.0    0.0   0.00 -0.054348    0.0    0.0  0.516854    0.0   
11              0.0    0.0   1.25 -0.054348    0.0    0.0  0.595506    0.0   
38              0.0    1.0  -0.50 -0.054348    0.0    0.0  1.505618    0.0   
40              0.0    1.0   0.75 -0.054348    0.0    0.0  1.584270    0.0   
71              0.0    1.0  -0.25 -0.054348    0.0    0.0  0.067416    0.0   
86              0.0    0.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   
88              0.0   16.0   0.00 -0.054348    0.0    0.0  0.258427    0.0   
89              0.0    1.0  -0.25 -0.054348    0.0    0.0  0.258427    0.0   
116             0.0    1.0   0.00 -0.054348    0.0    0.0  0.483146    0.0   
117             0.0    0.0  -0.50 -0.054348    0.0    0.0  0.483146    0.0   
141             0.0    0.0  -0.50 -0.054348    0.0    0.0  0.775281    0.0   
142             0.0    1.0  -0.75 -0.054348    0.0    0.0  0.775281    0.0   
4               0.0    1.0   1.25  0.913043    0.0    1.0  0.000000    0.0   
5               0.0    1.0   0.00  0.945652    0.0    1.0  0.000000    0.0   
9               0.0    0.0  -0.25  1.010870    0.0    0.0  0.000000    0.0   
12              0.0    1.0  -0.25  1.086957    0.0    0.0  0.000000    0.0   
37              0.0    0.0   1.00  0.097826    0.0    1.0  0.000000    0.0   
39              0.0    1.0   0.25  0.173913    0.0    1.0  0.000000    0.0   
72              0.0    1.0   1.75  0.902174    0.0    1.0  0.000000    0.0   
79              0.0    0.0   0.00  0.956522    0.0    1.0  0.000000    0.0   
87              0.0    0.0   0.50  1.152174    0.0    1.0  0.000000    0.0   
109             0.0    3.0   1.75  1.326087    0.0    1.0  0.000000    0.0   
114             0.0    0.0   1.25  1.358696    0.0    1.0  0.000000    0.0   
115             0.0    1.0   0.75  1.358696    0.0    1.0  0.000000    0.0   
128             0.0    0.0   1.25  1.500000    0.0    1.0  0.000000    0.0   
129             0.0    1.0   0.75  1.500000    0.0    1.0  0.000000    0.0   

       X_253  X_254  ...    X_2858    X_2859    X_2860    X_2861    X_2862  \
index                ...                                                     
3       -1.0   -1.0  ... -0.585118 -1.336788  1.159091  1.715374  1.636986   
6       -1.0   -1.0  ... -1.705924 -2.854922  1.424242  1.957184  1.041096   
10      -1.0   -1.0  ... -0.951125 -0.829016  1.204545  1.582338  0.993151   
11      -1.0   -1.0  ... -1.343554 -1.497409  1.090909  1.374600  1.109589   
38      -1.0   -1.0  ... -1.920884 -2.207254  0.954545  1.398276  1.383562   
40      -1.0   -1.0  ... -1.380046 -1.658031  1.628788  2.220402  1.767123   
71      -1.0   -1.0  ... -0.420824 -0.549223  1.492424  2.167816  1.863014   
86      -1.0   -1.0  ...  0.051022 -0.720207  1.492424  2.143966  1.369863   
88      -1.0   -1.0  ...  5.506263  3.642487  3.325758  3.852278  3.178082   
89      -1.0   -1.0  ...  0.291414  0.010363  1.446970  2.243647  1.671233   
116     -1.0   -1.0  ... -1.391573 -2.569948  1.416667  1.918647  1.561644   
117     -1.0   -1.0  ... -1.849230 -1.870466  1.750000  2.069828  1.993151   
141     -1.0   -1.0  ...  2.704854  1.316062  1.727273  2.173563  2.089041   
142      0.0   -1.0  ...  3.291153  2.523316  2.484848  2.879659  2.452055   
4        0.0    0.0  ...  0.117716 -0.689119  2.083333  1.851385  1.356164   
5        0.0    0.0  ... -1.153107 -1.388601  1.560606  1.792529  1.493151   
9        0.0    0.0  ... -0.074593  0.113990  1.083333  1.794540  1.684932   
12       0.0    0.0  ... -1.159318 -1.233161  1.090909  1.678161  1.801370   
37       0.0    0.0  ... -0.302514 -0.854922  1.106061  1.346921  0.883562   
39       0.0    0.0  ... -1.

In [405]:
TT10_idx = TT10['PRODUCT_CODE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])
TT10_idx

index
0        1
1        2
2       15
3       17
4       20
..     ...
238    301
239    305
240    307
241    308
242    309

[243 rows x 1 columns]

In [406]:
TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)
TT10

PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  ...  \
0             0.0  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
1             0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
2             0.0  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
3             0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
4             0.0  0.0 -0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
..            ...  ...  ...  ...  ...  ...  ...       ...  ...  ...  ...   
238           0.0  0.0 -0.2  0.0  0.0  0.0  0.0  1.000000  0.0  1.0  ...   
239           0.0  0.0 -0.8  0.0  0.0  0.0  0.0  1.000000  0.0  1.0  ...   
240           0.0  0.0 -0.8  0.0  0.0  0.0  0.0  0.833333  0.0  1.0  ...   
241           0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0  ...   
242           0.0  0.0 -1.6  0.0  0.0  0.0  0.0  1.000000  0.0  1.0  ...   

        X_926  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
0   -1.732246  -1.24    0.1  0.800000  1.000000    0.0  0.086956    0.0   
1    1.473129   1.90    0.0  0.015909  0.000000    0.0 -0.391304    0.0   
2    2.522073   1.00   -0.9 -0.343182  0.000000    0.0 -0.173913    0.0   
3    3.619002   1.00    0.0  0.490909  0.000000    1.0  0.043478    0.0   
4    3.346449   2.30   -0.9 -0.293182  0.000000    0.0  0.044927    0.0   
..        ...    ...    ...       ...       ...    ...       ...    ...   
238 -0.857965   0.18    0.1  0.818182  1.000000    0.0 -0.260870    0.0   
239 -0.520154  -0.94    0.0  0.859091  0.555556    0.0 -0.782609    0.0   
240 -0.919386  -0.52   -0.3 -0.222727  0.000000    0.0 -0.521739    0.0   
241 -0.275688  -1.14    0.0  0.102273  0.111111    0.0 -0.869565    0.0   
242 -0.472169  -0.10    0.1  0.245455  0.000000    0.0 -0.763768    0.0   

         HOUR  DAY_OF_WEEK  
0   -0.666667     0.000000  
1   -0.166667     0.000000  
2   -0.416667    -1.000000  
3    1.083333    -0.333333  
4   -0.750000     0.000000  
..        ...          ...  
238  0.416667     0.000000  
239  0.083333     0.333333  
240  0.500000     0.333333  
241  0.833333     0.333333  
242  0.916667     0.333333  

[243 rows x 668 columns]

In [407]:
TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')
TT10

PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  ...  \
index                                                                  ...   
1               0.0  0.0 -0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
2               0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
15              0.0  0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
17              0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
20              0.0  0.0 -0.2  0.0  0.0  1.0  0.0  0.000000  0.0  0.0  ...   
...             ...  ...  ...  ...  ...  ...  ...       ...  ...  ...  ...   
301             0.0  0.0 -0.2  0.0  0.0  0.0  0.0  1.000000  0.0  1.0  ...   
305             0.0  0.0 -0.8  0.0  0.0  0.0  0.0  1.000000  0.0  1.0  ...   
307             0.0  0.0 -0.8  0.0  0.0  0.0  0.0  0.833333  0.0  1.0  ...   
308             0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.000000  0.0  1.0  ...   
309             0.0  0.0 -1.6  0.0  0.0  0.0  0.0  1.000000  0.0  1.0  ...   

          X_926  X_927  X_928     X_929     X_930  X_931     X_932  X_933  \
index                                                                       
1     -1.732246  -1.24    0.1  0.800000  1.000000    0.0  0.086956    0.0   
2      1.473129   1.90    0.0  0.015909  0.000000    0.0 -0.391304    0.0   
15     2.522073   1.00   -0.9 -0.343182  0.000000    0.0 -0.173913    0.0   
17     3.619002   1.00    0.0  0.490909  0.000000    1.0  0.043478    0.0   
20     3.346449   2.30   -0.9 -0.293182  0.000000    0.0  0.044927    0.0   
...         ...    ...    ...       ...       ...    ...       ...    ...   
301   -0.857965   0.18    0.1  0.818182  1.000000    0.0 -0.260870    0.0   
305   -0.520154  -0.94    0.0  0.859091  0.555556    0.0 -0.782609    0.0   
307   -0.919386  -0.52   -0.3 -0.222727  0.000000    0.0 -0.521739    0.0   
308   -0.275688  -1.14    0.0  0.102273  0.111111    0.0 -0.869565    0.0   
309   -0.472169  -0.10    0.1  0.245455  0.000000    0.0 -0.763768    0.0   

           HOUR  DAY_OF_WEEK  
index                         
1     -0.666667     0.000000  
2     -0.166667     0.000000  
15    -0.416667    -1.000000  
17     1.083333    -0.333333  
20    -0.750000     0.000000  
...         ...          ...  
301    0.416667     0.000000  
305    0.083333     0.333333  
307    0.500000     0.333333  
308    0.833333     0.333333  
309    0.916667     0.333333  

[243 rows x 668 columns]

In [320]:
TT05 = TT05.to_numpy()
TT01 = TT01.to_numpy()
TT10 = TT10.to_numpy()

# T05

In [374]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [375]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
0             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
1             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
2             0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
3             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
4             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
..            ...    ...    ...    ...    ...       ...       ...       ...   
115           0.0   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
118           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
119           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   

        X_139     X_140     X_141  X_142  X_143  X_144  X_145     X_146  \
0   -0.024793 -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454   
1    0.024793 -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040   
2   -0.008264 -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877   
3    0.002755 -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990   
4   -0.002755 -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680   
..        ...       ...       ...    ...    ...    ...    ...       ...   
115 -1.049587 -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057   
116 -1.049587 -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895   
117 -1.044077 -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307   
118 -1.033058 -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895   
119 -1.082645 -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921   

     X_147     X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  \
0      0.0  0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0   
1      0.0 -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0   
2      0.0  0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0   
3      0.0  0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0   
4      0.0  0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0   
..     ...       ...       ...     ...    ...    ...    ...    ...    ...   
115    0.0  1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0   
116    0.0  1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0   
117    0.0  1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0   
118    0.0  1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0   
119    0.0  1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0   

     X_156  X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  \
0      0.0    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
1      0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
2      0.1    0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5   
3      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5   
4      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
115    0.0    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
116    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5   
117    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5   
118    0.0   -0.1    0.0   -1.0    0.1    0.0    0.0   -0.1    0.0   -0.5   
119    0.0    0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0.5   

     X_166  X_167  X_168  X_169  X_170  X_171  X_172  X_173  X_174  X_175  \
0      0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1      0.0   -1.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0   
2      0.0   -1.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0 

In [376]:
T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
index                                                                           
0               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
2               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
4               0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
6               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
8               0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
...             ...    ...    ...    ...    ...       ...       ...       ...   
549             0.0   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292   
550             0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
551             0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
552             0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
555             0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   

          X_139     X_140     X_141  X_142  X_143  X_144  X_145     X_146  \
index                                                                       
0     -0.024793 -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454   
2      0.024793 -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040   
4     -0.008264 -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877   
6      0.002755 -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990   
8     -0.002755 -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680   
...         ...       ...       ...    ...    ...    ...    ...       ...   
549   -1.049587 -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057   
550   -1.049587 -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895   
551   -1.044077 -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307   
552   -1.033058 -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895   
555   -1.082645 -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921   

       X_147     X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  \
index                                                                         
0        0.0  0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0   
2        0.0 -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0   
4        0.0  0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0   
6        0.0  0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0   
8        0.0  0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0   
...      ...       ...       ...     ...    ...    ...    ...    ...    ...   
549      0.0  1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0   
550      0.0  1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0   
551      0.0  1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0   
552      0.0  1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0   
555      0.0  1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0   

       X_156  X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  \
index                                                                         
0        0.0    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
2        0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
4        0.1    0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5   
6        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5   
8        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549      0.0    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5   
550      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5   
551      0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5   
552      0.0   -0.1    0.0   -1.0    0.1    0.0    0.0

In [377]:
#13
setup_rgs = setup(data = T05_data, target = T05_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [378]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [379]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [380]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMRegressor(random_state=414),
 RandomForestRegressor(n_jobs=-1, random_state=414),
 GradientBoostingRegressor(random_state=414),
 ExtraTreesRegressor(n_jobs=-1, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, predictor='auto', random_state=414,
              reg_alpha=0, reg_lambda=1, ...),
 AdaBoostRegressor(learning_rate=0.1, loss='exponential', n_estimators=200,
                   random_state=414)]

In [381]:
for model in T05_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654   
85            0.0    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007   
86            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751   
87            0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
88            0.0    0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388   
89            0.0   -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227   
90            0.0    0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643   
91            0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
92            0.0    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639   
93            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
94            0.0   -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922   
95            0.0    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042   
96            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
97            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
98            0.0    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656   
99            0.0    0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868   
100           0.0    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560   
101           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
102           0.0   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386   
103           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
104           0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
105           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   
106           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
107           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
108           0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
109           0.0    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862   
110           0.0    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312   
111           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
112           0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683   
113           0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
114           0.0    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951   
115           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
118           0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
119           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   

        X_139     X_140  ...    X_2866    X_2867    X_2868    X_2869  \
84   0.371901  0.551020  ...  0.234148  0.727368  0.660000  0.185721   
85  -0.079890  0.024943  ...  0.041757  0.067310  0.679286  0.161771   
86   0.019284  0.006803  ... -0.334364 -0.043308  0.215000  0.045639   
87  -1.628099 -1.340136  ...  0.035571 -0.078268  0.007857  0.082241   
88   0.190083  0.192744  ...  0.218064  0.332899  0.018571  0.009941   
89   0.933884  0.877551  ...  0.119703  0.240543  0.063571  0.000904   
90   0.757576  0.700680  ...  0.128982  0.267154  0.661429  0.084953   
91   0.278237  0.269841  ...  0.472935  0.075137  0.325714  0.050158   
92   1.071625  0.950113  ... -3.253634 -2.855205 -3.568571 -2.499322   
93   0.636364  0.596372  ...  0.254562  0.371511 -0.668571  0.057840   
94   0.008264 -0.002268  ... -3.253634 -2.855205 -3.568571 -2.499322   
95   0.520661  0.505669  ...  0.049180  0.144013  0.458571  0.056936   
96   0.024793 -0.029478  ... -0.829261 -0.942865 -0.535000 -0.848622   
97  -0.217631 -0.219955  ...  0.330653  0.058440  0.234286  0.063714   
9

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654   
85            0.0    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007   
86            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751   
87            0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
88            0.0    0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388   
89            0.0   -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227   
90            0.0    0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643   
91            0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
92            0.0    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639   
93            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
94            0.0   -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922   
95            0.0    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042   
96            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
97            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
98            0.0    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656   
99            0.0    0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868   
100           0.0    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560   
101           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
102           0.0   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386   
103           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
104           0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
105           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   
106           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
107           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
108           0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
109           0.0    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862   
110           0.0    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312   
111           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
112           0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683   
113           0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
114           0.0    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951   
115           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
118           0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
119           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   

        X_139     X_140  ...    X_2866    X_2867    X_2868    X_2869  \
84   0.371901  0.551020  ...  0.234148  0.727368  0.660000  0.185721   
85  -0.079890  0.024943  ...  0.041757  0.067310  0.679286  0.161771   
86   0.019284  0.006803  ... -0.334364 -0.043308  0.215000  0.045639   
87  -1.628099 -1.340136  ...  0.035571 -0.078268  0.007857  0.082241   
88   0.190083  0.192744  ...  0.218064  0.332899  0.018571  0.009941   
89   0.933884  0.877551  ...  0.119703  0.240543  0.063571  0.000904   
90   0.757576  0.700680  ...  0.128982  0.267154  0.661429  0.084953   
91   0.278237  0.269841  ...  0.472935  0.075137  0.325714  0.050158   
92   1.071625  0.950113  ... -3.253634 -2.855205 -3.568571 -2.499322   
93   0.636364  0.596372  ...  0.254562  0.371511 -0.668571  0.057840   
94   0.008264 -0.002268  ... -3.253634 -2.855205 -3.568571 -2.499322   
95   0.520661  0.505669  ...  0.049180  0.144013  0.458571  0.056936   
96   0.024793 -0.029478  ... -0.829261 -0.942865 -0.535000 -0.848622   
97  -0.217631 -0.219955  ...  0.330653  0.058440  0.234286  0.063714   
9

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654   
85            0.0    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007   
86            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751   
87            0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
88            0.0    0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388   
89            0.0   -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227   
90            0.0    0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643   
91            0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
92            0.0    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639   
93            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
94            0.0   -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922   
95            0.0    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042   
96            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
97            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
98            0.0    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656   
99            0.0    0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868   
100           0.0    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560   
101           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
102           0.0   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386   
103           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
104           0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
105           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   
106           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
107           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
108           0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
109           0.0    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862   
110           0.0    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312   
111           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
112           0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683   
113           0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
114           0.0    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951   
115           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
118           0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
119           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   

        X_139     X_140  ...    X_2866    X_2867    X_2868    X_2869  \
84   0.371901  0.551020  ...  0.234148  0.727368  0.660000  0.185721   
85  -0.079890  0.024943  ...  0.041757  0.067310  0.679286  0.161771   
86   0.019284  0.006803  ... -0.334364 -0.043308  0.215000  0.045639   
87  -1.628099 -1.340136  ...  0.035571 -0.078268  0.007857  0.082241   
88   0.190083  0.192744  ...  0.218064  0.332899  0.018571  0.009941   
89   0.933884  0.877551  ...  0.119703  0.240543  0.063571  0.000904   
90   0.757576  0.700680  ...  0.128982  0.267154  0.661429  0.084953   
91   0.278237  0.269841  ...  0.472935  0.075137  0.325714  0.050158   
92   1.071625  0.950113  ... -3.253634 -2.855205 -3.568571 -2.499322   
93   0.636364  0.596372  ...  0.254562  0.371511 -0.668571  0.057840   
94   0.008264 -0.002268  ... -3.253634 -2.855205 -3.568571 -2.499322   
95   0.520661  0.505669  ...  0.049180  0.144013  0.458571  0.056936   
96   0.024793 -0.029478  ... -0.829261 -0.942865 -0.535000 -0.848622   
97  -0.217631 -0.219955  ...  0.330653  0.058440  0.234286  0.063714   
9

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654   
85            0.0    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007   
86            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751   
87            0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
88            0.0    0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388   
89            0.0   -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227   
90            0.0    0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643   
91            0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
92            0.0    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639   
93            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
94            0.0   -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922   
95            0.0    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042   
96            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
97            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
98            0.0    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656   
99            0.0    0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868   
100           0.0    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560   
101           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
102           0.0   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386   
103           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
104           0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
105           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   
106           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
107           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
108           0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
109           0.0    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862   
110           0.0    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312   
111           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
112           0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683   
113           0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
114           0.0    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951   
115           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
118           0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
119           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   

        X_139     X_140  ...    X_2866    X_2867    X_2868    X_2869  \
84   0.371901  0.551020  ...  0.234148  0.727368  0.660000  0.185721   
85  -0.079890  0.024943  ...  0.041757  0.067310  0.679286  0.161771   
86   0.019284  0.006803  ... -0.334364 -0.043308  0.215000  0.045639   
87  -1.628099 -1.340136  ...  0.035571 -0.078268  0.007857  0.082241   
88   0.190083  0.192744  ...  0.218064  0.332899  0.018571  0.009941   
89   0.933884  0.877551  ...  0.119703  0.240543  0.063571  0.000904   
90   0.757576  0.700680  ...  0.128982  0.267154  0.661429  0.084953   
91   0.278237  0.269841  ...  0.472935  0.075137  0.325714  0.050158   
92   1.071625  0.950113  ... -3.253634 -2.855205 -3.568571 -2.499322   
93   0.636364  0.596372  ...  0.254562  0.371511 -0.668571  0.057840   
94   0.008264 -0.002268  ... -3.253634 -2.855205 -3.568571 -2.499322   
95   0.520661  0.505669  ...  0.049180  0.144013  0.458571  0.056936   
96   0.024793 -0.029478  ... -0.829261 -0.942865 -0.535000 -0.848622   
97  -0.217631 -0.219955  ...  0.330653  0.058440  0.234286  0.063714   
9

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654   
85            0.0    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007   
86            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751   
87            0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
88            0.0    0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388   
89            0.0   -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227   
90            0.0    0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643   
91            0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
92            0.0    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639   
93            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
94            0.0   -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922   
95            0.0    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042   
96            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
97            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
98            0.0    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656   
99            0.0    0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868   
100           0.0    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560   
101           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
102           0.0   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386   
103           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
104           0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
105           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   
106           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
107           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
108           0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
109           0.0    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862   
110           0.0    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312   
111           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
112           0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683   
113           0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
114           0.0    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951   
115           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
118           0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
119           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   

        X_139     X_140  ...    X_2866    X_2867    X_2868    X_2869  \
84   0.371901  0.551020  ...  0.234148  0.727368  0.660000  0.185721   
85  -0.079890  0.024943  ...  0.041757  0.067310  0.679286  0.161771   
86   0.019284  0.006803  ... -0.334364 -0.043308  0.215000  0.045639   
87  -1.628099 -1.340136  ...  0.035571 -0.078268  0.007857  0.082241   
88   0.190083  0.192744  ...  0.218064  0.332899  0.018571  0.009941   
89   0.933884  0.877551  ...  0.119703  0.240543  0.063571  0.000904   
90   0.757576  0.700680  ...  0.128982  0.267154  0.661429  0.084953   
91   0.278237  0.269841  ...  0.472935  0.075137  0.325714  0.050158   
92   1.071625  0.950113  ... -3.253634 -2.855205 -3.568571 -2.499322   
93   0.636364  0.596372  ...  0.254562  0.371511 -0.668571  0.057840   
94   0.008264 -0.002268  ... -3.253634 -2.855205 -3.568571 -2.499322   
95   0.520661  0.505669  ...  0.049180  0.144013  0.458571  0.056936   
96   0.024793 -0.029478  ... -0.829261 -0.942865 -0.535000 -0.848622   
97  -0.217631 -0.219955  ...  0.330653  0.058440  0.234286  0.063714   
9

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654   
85            0.0    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007   
86            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751   
87            0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
88            0.0    0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388   
89            0.0   -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227   
90            0.0    0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643   
91            0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
92            0.0    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639   
93            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
94            0.0   -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922   
95            0.0    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042   
96            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
97            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
98            0.0    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656   
99            0.0    0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868   
100           0.0    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560   
101           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
102           0.0   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386   
103           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
104           0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
105           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   
106           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
107           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
108           0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
109           0.0    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862   
110           0.0    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312   
111           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
112           0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683   
113           0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
114           0.0    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951   
115           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
118           0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
119           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   

        X_139     X_140  ...    X_2866    X_2867    X_2868    X_2869  \
84   0.371901  0.551020  ...  0.234148  0.727368  0.660000  0.185721   
85  -0.079890  0.024943  ...  0.041757  0.067310  0.679286  0.161771   
86   0.019284  0.006803  ... -0.334364 -0.043308  0.215000  0.045639   
87  -1.628099 -1.340136  ...  0.035571 -0.078268  0.007857  0.082241   
88   0.190083  0.192744  ...  0.218064  0.332899  0.018571  0.009941   
89   0.933884  0.877551  ...  0.119703  0.240543  0.063571  0.000904   
90   0.757576  0.700680  ...  0.128982  0.267154  0.661429  0.084953   
91   0.278237  0.269841  ...  0.472935  0.075137  0.325714  0.050158   
92   1.071625  0.950113  ... -3.253634 -2.855205 -3.568571 -2.499322   
93   0.636364  0.596372  ...  0.254562  0.371511 -0.668571  0.057840   
94   0.008264 -0.002268  ... -3.253634 -2.855205 -3.568571 -2.499322   
95   0.520661  0.505669  ...  0.049180  0.144013  0.458571  0.056936   
96   0.024793 -0.029478  ... -0.829261 -0.942865 -0.535000 -0.848622   
97  -0.217631 -0.219955  ...  0.330653  0.058440  0.234286  0.063714   
9

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
84            0.0    0.0    0.0    0.0    0.0  0.360041  0.347870  0.359654   
85            0.0    0.0    0.0   -1.0    0.0  0.648073  0.646045  0.649007   
86            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.202751   
87            0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
88            0.0    0.0    0.0    0.0    0.0  0.453347  0.451318  0.453388   
89            0.0   -1.0    0.0   -1.0    0.0  0.982759  0.980730  0.985227   
90            0.0    0.0    0.0    0.0    0.0  0.897566  0.895537  0.899643   
91            0.0    0.0    0.0    0.0    0.0  0.495943  0.493915  0.496179   
92            0.0    0.0    0.0    0.0    0.0  1.110548  1.108519  1.115639   
93            0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.795721   
94            0.0   -1.0   -1.0   -2.0    0.0 -0.149087 -0.151116 -0.157922   
95            0.0    0.0    0.0    0.0    0.0  0.757607  0.755578  0.759042   
96            0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
97            0.0   -1.0   -1.0   -1.0    0.0 -0.313387 -0.315416 -0.316862   
98            0.0    0.0    0.0    0.0    0.0  0.248479  0.250507  0.251656   
99            0.0    0.0    0.0    0.0    0.0  1.015213  1.013185  1.019868   
100           0.0    0.0    0.0    0.0    0.0 -0.301217 -0.299189 -0.300560   
101           0.0    0.0    0.0    0.0    0.0  0.280933  0.278905  0.280183   
102           0.0   -1.0    0.0   -1.0    0.0 -0.560852 -0.558824 -0.561386   
103           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
104           0.0    0.0    0.0    0.0    0.0 -0.412779 -0.414807 -0.416709   
105           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   
106           0.0   -1.0   -1.0   -1.0    0.0 -0.195740 -0.197769 -0.198675   
107           0.0    0.0    0.0    0.0    0.0  0.177485  0.175456  0.176261   
108           0.0    0.0    0.0   -1.0    0.0  0.266734  0.264706  0.265920   
109           0.0    0.0    0.0    0.0    0.0 -0.313387 -0.315416 -0.316862   
110           0.0    0.0    0.0    0.0    0.0 -0.445233 -0.447262 -0.449312   
111           0.0   -1.0    0.0   -1.0    0.0 -0.542596 -0.544625 -0.547122   
112           0.0    0.0    0.0    0.0    0.0  0.792089  0.790061  0.793683   
113           0.0    0.0    0.0   -1.0    0.0  0.191684  0.189655  0.190525   
114           0.0    0.0    0.0    0.0    0.0  0.591278  0.577079  0.591951   
115           0.0    0.0    0.0   -1.0    0.0  0.406694  0.404665  0.402445   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.045639 -0.047667 -0.047886   
118           0.0    0.0    0.0    0.0    0.0  0.901623  0.899594  0.903719   
119           0.0    0.0    0.0    0.0    0.0  0.621704  0.619675  0.622517   

        X_139     X_140  ...    X_2866    X_2867    X_2868    X_2869  \
84   0.371901  0.551020  ...  0.234148  0.727368  0.660000  0.185721   
85  -0.079890  0.024943  ...  0.041757  0.067310  0.679286  0.161771   
86   0.019284  0.006803  ... -0.334364 -0.043308  0.215000  0.045639   
87  -1.628099 -1.340136  ...  0.035571 -0.078268  0.007857  0.082241   
88   0.190083  0.192744  ...  0.218064  0.332899  0.018571  0.009941   
89   0.933884  0.877551  ...  0.119703  0.240543  0.063571  0.000904   
90   0.757576  0.700680  ...  0.128982  0.267154  0.661429  0.084953   
91   0.278237  0.269841  ...  0.472935  0.075137  0.325714  0.050158   
92   1.071625  0.950113  ... -3.253634 -2.855205 -3.568571 -2.499322   
93   0.636364  0.596372  ...  0.254562  0.371511 -0.668571  0.057840   
94   0.008264 -0.002268  ... -3.253634 -2.855205 -3.568571 -2.499322   
95   0.520661  0.505669  ...  0.049180  0.144013  0.458571  0.056936   
96   0.024793 -0.029478  ... -0.829261 -0.942865 -0.535000 -0.848622   
97  -0.217631 -0.219955  ...  0.330653  0.058440  0.234286  0.063714   
9

In [382]:
T05_final_regression_model = finalize_model(T05_model_et)

In [383]:
T05_prediction = predict_model(T05_final_regression_model, data=T05_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)
T05_prediction

PRODUCT_CODE  X_132  X_133  X_134  X_135     X_136     X_137     X_138  \
0             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
1             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
2             0.0   -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864   
3             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
4             0.0   -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864   
..            ...    ...    ...    ...    ...       ...       ...       ...   
115           0.0   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292   
116           0.0   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255   
117           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
118           0.0   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179   
119           0.0   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066   

        X_139     X_140  ...  X_2865    X_2866    X_2867    X_2868    X_2869  \
0   -0.024793 -0.052154  ...     1.0 -0.819981 -0.721628 -1.242857 -0.958879   
1    0.024793 -0.029478  ...     1.0 -0.829261 -0.942865 -0.535000 -0.848622   
2   -0.008264 -0.043084  ...     0.0 -0.859573 -0.669450 -0.216429 -1.004067   
3    0.002755 -0.043084  ...     1.0 -1.243118 -0.693973 -0.828571 -1.106191   
4   -0.002755 -0.047619  ...     1.0 -0.639963 -0.602661  0.402857 -0.996385   
..        ...       ...  ...     ...       ...       ...       ...       ...   
115 -1.049587 -0.882086  ...    -8.0  0.023198  0.080355  0.227143  0.044736   
116 -1.049587 -0.891156  ...   -10.0  0.000928 -0.084529  0.524286  0.057840   
117 -1.044077 -0.886621  ...     0.0 -0.019487  0.079311  0.322143 -0.214641   
118 -1.033058 -0.877551  ...     0.0  0.064646  0.218106 -0.007857  0.106191   
119 -1.082645 -0.877551  ...     1.0 -3.253634 -2.855205 -3.568571 -2.499322   

        X_2870  X_2871      HOUR  DAY_OF_WEEK  prediction_label  
0     3.252475    -1.0 -0.222222         -0.6          0.533433  
1     3.396039    -1.0 -0.222222         -0.6          0.531267  
2     3.054456    -1.0 -0.222222         -0.6          0.531590  
3     3.044554    -1.0 -0.111111         -0.6          0.533665  
4     3.433168    -1.0 -0.111111         -0.6          0.531821  
..         ...     ...       ...          ...               ...  
115   0.346535     0.0  0.111111          0.2          0.533711  
116   0.544554     0.0  0.111111          0.2          0.533695  
117  -0.519802     0.0  0.222222          0.2          0.525271  
118  -0.368812     0.0  0.777778          0.2          0.529806  
119 -15.997525     0.0  0.555556          0.2          0.521406  

[120 rows x 1960 columns]

In [428]:
T05_datas = T05_prediction['prediction_label']
T05_datas = pd.DataFrame(T05_datas.values, columns = ['Y_Quality'])
T05_datas

Y_Quality
0     0.533433
1     0.531267
2     0.531590
3     0.533665
4     0.531821
..         ...
115   0.533711
116   0.533695
117   0.525271
118   0.529806
119   0.521406

[120 rows x 1 columns]

In [429]:
from pycaret.regression import *
TT05_prediction = predict_model(T05_final_regression_model, data=TT05)

In [438]:
TT05s = TT05s.reshape(-1, 1)

In [431]:
TT05_y_class = pd.DataFrame(TT05, columns = ['PRODUCT_CODE'])
TT05_idx = TT05_y_class.index
TT05_y_class = TT05_y_class.reset_index()
TT05_prediction = pd.concat([TT05_prediction, TT05_y_class], axis = 1)
TT05_prediction = TT05_prediction.set_index('index')
TT05_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT05s = TT05_prediction['prediction_label']

In [432]:
TT05s = TT05s.to_numpy()

In [433]:
#T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1).to_numpy()
T05_datas = T05_datas.to_numpy()
T05_class = T05['Y_Class'].to_numpy()

In [434]:
T05_xtrain, T05_xtest, T05_ytrain, T05_ytest = train_test_split(T05_datas, T05_class, test_size = 0.1, random_state = 4)

In [443]:
T05_class

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 0, 1, 1, 2, 2, 1, 1, 0, 0, 0,
       0, 0, 2, 1, 0, 1, 1, 0, 1, 1, 1, 2, 2, 1, 1, 0, 1, 1, 1, 1, 1, 1,
       0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 2, 2, 2, 2,
       2, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       2, 1, 2, 2, 2, 2, 2, 2, 2, 0, 0, 0, 2, 1, 2, 2, 2, 1, 1, 1, 0, 0,
       0, 0, 0, 0, 0, 1, 1, 1, 1, 0], dtype=int64)

In [435]:
T05_datas

array([[0.53343332],
       [0.53126669],
       [0.53159046],
       [0.53366506],
       [0.53182065],
       [0.5315032 ],
       [0.53363174],
       [0.53125399],
       [0.53405398],
       [0.53216982],
       [0.53117937],
       [0.5441286 ],
       [0.52152383],
       [0.52634603],
       [0.52881747],
       [0.53862858],
       [0.53773332],
       [0.53016669],
       [0.53167939],
       [0.51671112],
       [0.51945078],
       [0.5189603 ],
       [0.51980954],
       [0.52125871],
       [0.53540474],
       [0.52739841],
       [0.52154446],
       [0.52549362],
       [0.52509522],
       [0.51508254],
       [0.52788728],
       [0.52913016],
       [0.52655876],
       [0.53704602],
       [0.53596509],
       [0.52686828],
       [0.5292365 ],
       [0.5223    ],
       [0.52903491],
       [0.52833968],
       [0.5309    ],
       [0.528027  ],
       [0.53020161],
       [0.53292859],
       [0.52456665],
       [0.53149205],
       [0.52085555],
       [0.524

In [442]:
T05_tab_clf = TabNetClassifier(
    seed = 4,
    momentum = 0.1,
    gamma = 2.0,
    n_steps = 5,
    n_d = 32,
    n_a = 32,
    lambda_sparse = 1e-3,
    optimizer_fn = torch.optim.Adam,
    optimizer_params = dict(lr=1e-2),
    scheduler_params = {
        "step_size" : 10,
        "gamma" : 0.9
    },
    scheduler_fn = torch.optim.lr_scheduler.StepLR,
    mask_type = 'sparsemax',
    verbose = True
)
T05_tab_clf.fit(
    T05_xtrain, T05_ytrain,
    eval_set = [(T05_xtest, T05_ytest)],
    max_epochs = 100, patience = 20,
    batch_size = 128, virtual_batch_size = 32,
    num_workers = 0,
    weights = 1
)
T05_preds = T05_tab_clf.predict(TT05s)
T05_preds

Device used : cpu
epoch 0  | loss: 2.30793 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 1  | loss: 0.31453 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 2  | loss: 0.28509 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 3  | loss: 0.49606 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 4  | loss: 0.29661 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 5  | loss: 0.18421 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 6  | loss: 0.5373  | val_0_accuracy: 0.41667 |  0:00:00s
epoch 7  | loss: 0.24176 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 8  | loss: 0.21156 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 9  | loss: 0.23134 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 10 | loss: 0.31473 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 11 | loss: 0.38773 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 12 | loss: 0.14276 | val_0_accuracy: 0.41667 |  0:00:00s
epoch 13 | loss: 0.3902  | val_0_accuracy: 0.41667 |  0:00:00s
epoch 14 | loss: 0.281   | val_0_accuracy: 0.41667 |  0:00:00s
epoch 15 | loss: 0.23117 | val_0_accu

array([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2], dtype=int64)

In [449]:
T05_svm = svm.SVC()
T05_svm.fit(T05_datas, T05_class)
T05_svm.predict(T05_xtrain)

array([2, 2, 0, 1, 1, 0, 2, 0, 0, 1, 2, 1, 2, 1, 0, 0, 2, 0, 0, 0, 0, 1,
       2, 1, 0, 1, 2, 1, 2, 2, 0, 0, 0, 0, 1, 1, 0, 2, 2, 0, 0, 1, 1, 2,
       1, 0, 1, 2, 2, 1, 1, 0, 2, 1, 1, 2, 1, 0, 0, 0, 0, 1, 2, 1, 0, 1,
       2, 2, 1, 1, 1, 1, 0, 2, 0, 1, 1, 0, 2, 0, 2, 0, 2, 0, 1, 1, 1, 1,
       1, 0, 0, 1, 1, 0, 1, 1, 2, 2, 1, 1, 0, 0, 2, 2, 1, 1, 0, 0],
      dtype=int64)

# T01

In [354]:
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1).to_numpy()
T01_target = T01['Y_Class'].to_numpy()

In [355]:
T01_xtrain, T01_xtest, T01_ytrain, T01_ytest = train_test_split(T01_data, T01_target, test_size = 0.1, random_state = 4)

In [356]:
T01_tab_clf = TabNetClassifier(
    seed = 4,
    momentum = 0.05,
    gamma = 2.0,
    n_steps = 4,
    n_d = 32,
    n_a = 32,
    lambda_sparse = 1e-4,
    optimizer_fn = torch.optim.Adam,
    optimizer_params = dict(lr=1e-3),
    scheduler_params = {
        "step_size" : 150,
        "gamma" : 0.9
    },
    scheduler_fn = torch.optim.lr_scheduler.StepLR,
    mask_type = 'sparsemax',
    verbose = True
)
T01_tab_clf.fit(
    T01_xtrain, T01_ytrain,
    eval_set = [(T01_xtest, T01_ytest)],
    max_epochs = 100, patience = 20,
    batch_size = 1024, virtual_batch_size = 64,
    num_workers = 0,
    weights = 1
)
T01_preds = T01_tab_clf.predict(TT01)
T01_preds

Device used : cpu
epoch 0  | loss: 3.59125 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 1  | loss: 3.2236  | val_0_accuracy: 0.53846 |  0:00:00s
epoch 2  | loss: 3.15066 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 3  | loss: 3.49935 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 4  | loss: 3.19097 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 5  | loss: 3.13291 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 6  | loss: 2.9762  | val_0_accuracy: 0.53846 |  0:00:00s
epoch 7  | loss: 3.17559 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 8  | loss: 3.29254 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 9  | loss: 3.04566 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 10 | loss: 3.24934 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 11 | loss: 2.78231 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 12 | loss: 3.33777 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 13 | loss: 3.05642 | val_0_accuracy: 0.61538 |  0:00:00s
epoch 14 | loss: 2.75289 | val_0_accuracy: 0.53846 |  0:00:00s
epoch 15 | loss: 3.48838 | val_0_accu

array([1, 0, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 2, 0, 0, 2, 0, 0, 1, 0,
       1, 1, 1, 1, 1, 0], dtype=int64)

# T10

In [362]:
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1).to_numpy()
T10_target = T10['Y_Class'].to_numpy()

In [363]:
T10_xtrain, T10_xtest, T10_ytrain, T10_ytest = train_test_split(T10_data, T10_target, test_size = 0.1, random_state = 4)

In [372]:
T10_tab_clf = TabNetClassifier(
    seed = 4,
    momentum = 0.1,
    gamma = 1.5,
    n_steps = 3,
    n_d = 32,
    n_a = 32,
    lambda_sparse = 1e-3,
    optimizer_fn = torch.optim.Adam,
    optimizer_params = dict(lr=1e-2),
    scheduler_params = {
        "step_size" : 100,
        "gamma" : 0.5
    },
    scheduler_fn = torch.optim.lr_scheduler.StepLR,
    mask_type = 'sparsemax',
    verbose = True
)
T10_tab_clf.fit(
    T10_xtrain, T10_ytrain,
    eval_set = [(T10_xtest, T10_ytest)],
    max_epochs = 100, patience = 20,
    batch_size = 512, virtual_batch_size = 64,
    num_workers = 0,
    weights = 1
)
T10_preds = T10_tab_clf.predict(TT10)
T10_preds

Device used : cpu
epoch 0  | loss: 1.45576 | val_0_accuracy: 0.54286 |  0:00:00s
epoch 1  | loss: 1.37784 | val_0_accuracy: 0.14286 |  0:00:00s
epoch 2  | loss: 1.54061 | val_0_accuracy: 0.37143 |  0:00:00s
epoch 3  | loss: 1.40633 | val_0_accuracy: 0.28571 |  0:00:00s
epoch 4  | loss: 1.45041 | val_0_accuracy: 0.14286 |  0:00:00s
epoch 5  | loss: 1.27782 | val_0_accuracy: 0.68571 |  0:00:00s
epoch 6  | loss: 1.3295  | val_0_accuracy: 0.77143 |  0:00:00s
epoch 7  | loss: 1.27534 | val_0_accuracy: 0.37143 |  0:00:00s
epoch 8  | loss: 1.25608 | val_0_accuracy: 0.11429 |  0:00:00s
epoch 9  | loss: 1.26735 | val_0_accuracy: 0.14286 |  0:00:00s
epoch 10 | loss: 1.27623 | val_0_accuracy: 0.45714 |  0:00:00s
epoch 11 | loss: 1.20849 | val_0_accuracy: 0.22857 |  0:00:00s
epoch 12 | loss: 1.21357 | val_0_accuracy: 0.11429 |  0:00:01s
epoch 13 | loss: 1.21695 | val_0_accuracy: 0.2     |  0:00:01s
epoch 14 | loss: 1.20615 | val_0_accuracy: 0.11429 |  0:00:01s
epoch 15 | loss: 1.24358 | val_0_accu

array([2, 1, 0, 1, 0, 2, 0, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 0, 2, 2, 0, 1,
       2, 0, 0, 1, 2, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1,
       1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0,
       0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 2, 1, 1, 1,
       1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 2, 0, 0, 0, 0, 1, 1, 0,
       1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 0, 2, 0, 0, 0, 1, 1, 0, 1, 1, 0, 0,
       0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1,
       0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1,
       1, 0, 2, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0,
       0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0,
       0, 2, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1,
       0], dtype=int64)

In [373]:
T10_preds

array([2, 1, 0, 1, 0, 2, 0, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 0, 2, 2, 0, 1,
       2, 0, 0, 1, 2, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1,
       1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0,
       0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 2, 1, 1, 1,
       1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 2, 0, 0, 0, 0, 1, 1, 0,
       1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 0, 2, 0, 0, 0, 1, 1, 0, 1, 1, 0, 0,
       0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1,
       0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1,
       1, 0, 2, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0,
       0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0,
       0, 2, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1,
       0], dtype=int64)